In [26]:
import ibis
from ibis import _
import streamlit as st

conn = ibis.duckdb.connect(extensions=["spatial"])

state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
county_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-county.parquet"
states = conn.read_parquet(state_boundaries).rename(state_id = "STUSPS", state = "NAME")
county = conn.read_parquet(county_boundaries).rename(county = "NAMELSAD", state = "STATE_NAME")

localities_boundaries = "us_localities.parquet"
locality = conn.read_parquet(localities_boundaries)


votes = conn.read_csv("landvote.csv")

In [27]:
vote_county = (votes
               .filter(_["Jurisdiction Type"] == "County")
               .rename(county = "Jurisdiction Name", state_id = "State")
               .mutate(key = _.county + ibis.literal('-') + _.state_id)
               .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
               .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
               .mutate(log_amount=_.amount_n.log())
               .mutate(year=_['Date'].year().cast('int32'))
               .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
               )
df_county = (county
            .join(states.select("state", "state_id"), "state")
            .mutate(key = _.county + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_county, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("County"))
            .cast({"geometry": "geometry"})
             )


In [28]:
vote_local = (votes
                .filter(_["Jurisdiction Type"] == "Municipal")
                .rename(city = "Jurisdiction Name", state_id = "State")
                .mutate(key = _.city + ibis.literal('-') + _.state_id)
                .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
                .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
                .mutate(log_amount=_.amount_n.log())
                .mutate(year=_['Date'].year().cast('int32'))
                .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
                )

df_local = (locality
            .mutate(key = _.name + ibis.literal('-') + _.state_id)
            .select('key', 'geometry')
            .right_join(vote_local, "key")
            .drop('key_right')
            .mutate(jurisdiction = ibis.literal("Municipal"))
            .cast({"geometry": "geometry"})
            
            )


In [29]:
df = df_county.union(df_local)


In [12]:
gdf = df.execute()

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

In [31]:
votes.drop("Total Funds )

['State',
 'Jurisdiction Name',
 'Jurisdiction Type',
 'Date',
 'Description',
 'Finance Mechanism',
 '"Other" Comment',
 'Purpose',
 'Total Funds at Stake',
 'Conservation Funds at Stake',
 'Total Funds Approved',
 'Conservation Funds Approved',
 'Pass?',
 'Status',
 '% Yes',
 '% No',
 'Notes',
 'Voted Acq. Measure',
 'column18']

In [20]:
import subprocess
import os
from huggingface_hub import HfApi, login
import streamlit as st

login(st.secrets["HF_TOKEN"])
# api = HfApi(add_to_git_credential=False)
api = HfApi()

def hf_upload(file, repo_id):
    info = api.upload_file(
            path_or_fileobj=file,
            path_in_repo=file,
            repo_id=repo_id,
            repo_type="dataset",
        )
def generate_pmtiles(input_file, output_file, max_zoom=12):
    # Ensure Tippecanoe is installed
    if subprocess.call(["which", "tippecanoe"], stdout=subprocess.DEVNULL) != 0:
        raise RuntimeError("Tippecanoe is not installed or not in PATH")

    # Construct the Tippecanoe command
    command = [
        "tippecanoe",
        "-o", output_file,
        "-z", str(max_zoom),
        "--drop-densest-as-needed",
        "--extend-zooms-if-still-dropping",
        "--force",
        input_file
    ]

    # Run Tippecanoe
    try:
        subprocess.run(command, check=True)
        print(f"Successfully generated PMTiles file: {output_file}")
    except subprocess.CalledProcessError as e:
        print(f"Error running Tippecanoe: {e}")



The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/jovyan/.cache/huggingface/token
Login successful


In [ ]:
df.execute().to_file("vote.geojson")
generate_pmtiles("vote.geojson", "vote.pmtiles")
hf_upload("vote.pmtiles", "boettiger-lab/landvote")



In [25]:
import leafmap.maplibregl as leafmap
import geopandas
url = "https://huggingface.co/datasets/boettiger-lab/landvote/resolve/main/vote.geojson"

conn.read_geo(url).filter
#gpf = geopandas.read_file(url, engine="pyogrio")


DatabaseTable: ibis_read_geo_pamy33s53vaepploan6xzko2mu
  key          string
  Status       string
  yes          string
  year         int32
  amount       string
  log_amount   float64
  jurisdiction string
  geom         geospatial:geometry

In [18]:
gpf.to_file("vote.geojson")

In [21]:
generate_pmtiles("vote.geojson", "vote.pmtiles")


For layer 0, using name "vote"
vote.geojson:496: null geometry (additional not reported): in JSON object {"type":"Feature","properties":{"key":null,"Status":"Fail","yes":"43.668463401297%","year":1990,"amount":null,"log_amount":null,"jurisdiction":"County"},"geometry":null}
2195 features, 10372266 bytes of geometry, 95306 bytes of string pool
  99.9%  12/1136/1649  


Successfully generated PMTiles file: vote.pmtiles


In [22]:
gdf = geopandas.read_file("vote.pmtiles", engine="pyogrio")
gdf.crs

<Projected CRS: EPSG:3857>
Name: WGS 84 / Pseudo-Mercator
Axis Info [cartesian]:
- X[east]: Easting (metre)
- Y[north]: Northing (metre)
Area of Use:
- name: World between 85.06°S and 85.06°N.
- bounds: (-180.0, -85.06, 180.0, 85.06)
Coordinate Operation:
- name: Popular Visualisation Pseudo-Mercator
- method: Popular Visualisation Pseudo Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")

url = "https://huggingface.co/datasets/boettiger-lab/landvote/resolve/main/vote.pmtiles"

#gdf = df.filter(_.year==1988).execute()
#gdf.to_file("vote.geojson")

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint = {"fill-extrusion-color": outcome, 
         "fill-extrusion-opacity": 0.7,
         "fill-extrusion-height": ["*", ["get", "log_amount"], 5000],
        }
style = {
    "layers": [
        {
            "id": "votes",
            "source": "vote",
            "source-layer": "vote",
            "type": "fill-extrusion",
            "filter": [
                "==",
                ["get", "year"],
                1988,
            ],  # only show buildings with height info
            "paint": paint
        },
    ],
}

m.add_pmtiles(
    url,
    style=style,
    visible=True,
    opacity=1.0,
    tooltip=True,
    fit_bounds=False,
)
#m.add_layer_control()
m



#m.add_geojson("vote.geojson", "fill-extrusion", paint = paint)
#m.add_gdf(gdf, "fill-extrusion", paint = paint)
#m